In [77]:
import sqlite3

import pandas as pd

from sklearn.feature_extraction.text import CountVectorizer

# CONFIG
DB_PATH = '1_after_cleaning_databases/1000_devices_cleaned.db'
TABLE_NAME = 'css_attribute'
OUTPUT_NAME = 'feature_matrix'

## PANDAS
pd.set_option('future.no_silent_downcasting', True)
# Set pandas options to display the full DataFrame
pd.set_option('display.max_rows', None)  # Show all rows
pd.set_option('display.max_columns', None)  # Show all columns
pd.set_option('display.width', None)  # Disable line wrapping
pd.set_option('display.max_colwidth', None)  # Show full content in each column
pd.set_option('display.max_seq_item', 100000)  # Show all items in a sequence (e.g., lists, dictionaries)

# Optionally, increase the display buffer size
pd.set_option('display.max_info_columns', 100000)  # Show all columns in df.info()

# If you have very large dataframes, increasing this might help
pd.set_option('display.max_rows', 1000)  # You can change 1000 to a higher value if needed

### Functions

#### Loading data from sqlite to pandas dataframe

In [78]:
def load_sqlite_to_dataframe(db_path, table_name):
    conn = sqlite3.connect(db_path)
    df = pd.read_sql(f"SELECT * FROM {table_name}", conn)
    conn.close()
    return df

#### Changing boolean values to 1 and 0

In [79]:
def convert_booleans(value):
    true_values = {'enabled'}
    false_values = {'disabled'}

    if isinstance(value, str):
        val_lower = value.lower()
        if val_lower in true_values:
            return 1
        elif val_lower in false_values:
            return 0
    return value

#### Constructing feature matrix

In [80]:
def create_feature_matrix(df):
    # Handle fonts
    fonts = (
        df[df['attribute'] == 'font']
        .groupby('session_id')['value']
        .apply(lambda x: ';'.join(sorted(set(x))))
        .reset_index()
    )

    # replace spaces in font names with underscores
    fonts['value'] = fonts['value'].str.replace(' ', '_', regex=False)

    # Rest of features
    non_fonts = df[df['attribute'] != 'font'].copy()
    non_fonts['feature_name'] = non_fonts['source'] + ':' + non_fonts['attribute']

    # Apply boolean conversion
    non_fonts['value'] = non_fonts['value'].apply(convert_booleans)

    # Pivot table
    pivot = non_fonts.pivot_table(index='session_id',
                                  columns='feature_name',
                                  values='value',
                                  aggfunc='first').reset_index()

    # Merge fonts back
    full_df = pivot.merge(fonts, on='session_id', how='left')

    full_df.rename(columns={'value': 'fonts'}, inplace=True)

    return full_df

#### Changing font values to one-hot encoding

In [81]:
def vectorize_fonts(df, font_column='fonts'):
    vectorizer = CountVectorizer(tokenizer=lambda x: [token.strip() for token in x.split(';') if token.strip()])
    font_features = vectorizer.fit_transform(df[font_column].fillna(''))

    font_df = pd.DataFrame(
        font_features.toarray(),
        columns=[f'css:font_{f}' for f in vectorizer.get_feature_names_out()],
        index=df.index
    )

    font_df['css:font_vector'] = font_df.astype(str).agg(''.join, axis=1)

    df = df.drop(columns=[font_column]).join(font_df)
    return df

#### Cleaning feature types

In [82]:
def clean_feature_types(df):
    for col in df.columns:
        # todo bedzie trzeba na to spojrzec gdy dojda kolejne atrybuty bo jest to takie niezbyt uniwersalne
        if col.startswith('css:env') or col.startswith('js:env') or 'width' in col or 'height' in col:
            df[col] = pd.to_numeric(df[col], errors='coerce')

    # Fill missing numeric with -1
    numeric_cols = df.select_dtypes(include='number').columns
    df[numeric_cols] = df[numeric_cols].fillna(-1)

    # Fill missing non-numeric with empty string
    object_cols = df.select_dtypes(include='object').columns
    df[object_cols] = df[object_cols].fillna('')

    df = df.infer_objects()

    return df

#### Save datagframe to parquet

In [83]:
def save_features(df):
    df.to_parquet(f'2_after_feature_extraction/{OUTPUT_NAME}.parquet')
    df.to_csv(f'2_after_feature_extraction/{OUTPUT_NAME}.csv', index=False)

### Execution

In [84]:
# Load data
df_raw = load_sqlite_to_dataframe(DB_PATH, TABLE_NAME)

In [85]:
# Create feature matrix
df_features = create_feature_matrix(df_raw)

In [86]:
df_features

session_id browserstack:browser  \
0    0041b5e2-06c3-43a8-a837-cc0f23e9d1e9               chrome   
1    006ec0f9-9ad5-457d-8d6a-df7958ec7975               chrome   
2    007746e4-32b0-4f39-b768-200351c74882                 edge   
3    008d5537-1e12-48a5-a32f-ce831b21c74e      chromium_iphone   
4    00b748c3-5c91-43d2-b603-ae43d9fd4be2               chrome   
5    00deeea6-4055-44c5-9f50-e974686dc419       chrome_android   
6    00e79661-0a6d-411c-b229-c7a71ca4da3d              firefox   
7    0144b7d8-0cdd-4841-8438-9c21d4de3426               chrome   
8    019ef33d-bdb3-48b8-ab32-b2a42918802c               chrome   
9    01eda466-aa28-41a1-a024-555bc9783c77                 edge   
10   020f4098-0bad-486b-bd66-c998acf526e2              firefox   
11   021a5d7b-ec24-41b8-b06a-8be7b5ade747              firefox   
12   02a3540b-9693-41ca-aadc-081e82171b9c              firefox   
13   02eb43f6-0aed-4e25-b41c-12d1c7d1f82c              firefox   
14   02f9b40b-353f-46d5-b3e6-891e763c0a59              firefox   
15   02fa3239-8e18-4ace-9e48-96bc16724bf2               chrome   
16   0311a0d9-ff4d-49b6-8646-97ecb9ee47c3               chrome   
17   03163c06-3ac5-4d10-8d04-3ec6c89838dd                 edge   
18   03a3a0a3-49ab-4c19-9ba4-416a796fc9d4               chrome   
19   03cd6f2e-98fc-4b62-999a-e43619bcc5d8                 edge   
20   041595e5-b47c-4cc7-8640-c3116ebb34a4       chrome_android   
21   0416866e-8d82-4bbb-9556-4c4d42b69684              samsung   
22   042fd51e-8a43-481a-9b60-f3cc8710156f               chrome   
23   0472a8f8-8331-40f0-ba65-1c15f6925984                 edge   
24   053dbd23-1834-408d-be2d-38f74514ab30              firefox   
25   054c602e-3a2e-4556-b3b2-71b7495ac20a               chrome   
26   0571484b-2fa1-46d5-8a88-beb4e141feb7              firefox   
27   058e2e4b-7970-492f-a686-33120b6bd061               chrome   
28   05f924cd-8afa-49a8-a7c5-2138fc7df318               chrome   
29   06179079-5f42-48a1-b82d-851666958df3               chrome   
30   062359d8-6b9f-4133-8ebb-3463acb7442b                 edge   
31   06304e52-fae5-413d-b96c-339704a6b903                 edge   
32   066be6eb-12dc-4cef-b6ca-e89a0f872219                 edge   
33   06b80a18-e2c2-441a-a4ed-537b820e7470               chrome   
34   07083edc-9be7-43de-97c9-33fd37957ea1               chrome   
35   0733589f-9de3-414a-ac72-8acf1acdf6c6                 edge   
36   07c995d9-7466-4f22-8f24-a24a6e05f252               chrome   
37   07cab88b-a972-40f5-9832-1b609a3d03fe                 edge   
38   07fbcedc-5cad-4060-a363-1dfb64b93584               chrome   
39   083ecb4c-49e3-4004-87a2-dcf0c3e994cc               chrome   
40   083fd301-571f-4600-bc0b-3e8a9733f5a1               chrome   
41   08ce911a-0456-480d-a90b-d68b7963aa95               chrome   
42   09a0a787-0238-4d20-b87d-b604083bbaac                 edge   
43   09b45bb7-b576-4658-a690-81ff10acb8cb               chrome   
44   09f5bf4e-734c-4509-afea-d5dcee834eaa       chrome_android   
45   0a84a541-4ebd-4639-881f-e053bfd1a080                 edge   
46   0a95ca49-9430-411b-9ff7-c9a84efaf278              firefox   
47   0abb720d-f4a9-4a4f-8019-243cc1faff4f               chrome   
48   0af82d59-cf83-4fa8-b383-2457426346e2               chrome   
49   0b0a448a-d75e-4366-8742-05d57a57cd1c               chrome   
50   0bc19261-a5cc-4987-90e5-3ec33afda07f               chrome   
51   0c0ee4e7-de6e-4443-94d3-0d3a4b56c362                 ipad   
52   0c2360ed-6fc1-4662-a1af-b03661fbf55a       chrome_android   
53   0c3bd07d-9e71-4c24-ab7f-bc35a5e1c71d                 edge   
54   0c43c430-579d-448c-81bd-8c9bd4c002e0              firefox   
55   0c73f830-f7d6-4f2b-985d-3309088eb90e              firefox   
56   0c8495a0-2771-496b-b087-c9f7695f6711        chromium_ipad   
57   0c9b4157-f681-4734-a327-d0f5fdcaa883                 edge   
58   0cdab11b-fb1c-45a8-9d14-87a5181bfef4              firefox   
59   0d1019c7-41b0-4d12-a44e-1c9a02b403a3               iphone   
60   

In [87]:
# Vectorize fonts
df_features = vectorize_fonts(df_features)

C:\Programs\TBO\tbo-task1\Python\Flask_Book_Library\.venv\Lib\site-packages\sklearn\feature_extraction\text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


In [88]:
# Clean feature types
df_ready = clean_feature_types(df_features)

In [89]:
# test Output
print(f"Shape of feature matrix: {df_ready.shape}")
display(df_ready.head())

Shape of feature matrix: (932, 119)


session_id browserstack:browser  \
0  0041b5e2-06c3-43a8-a837-cc0f23e9d1e9               chrome   
1  006ec0f9-9ad5-457d-8d6a-df7958ec7975               chrome   
2  007746e4-32b0-4f39-b768-200351c74882                 edge   
3  008d5537-1e12-48a5-a32f-ce831b21c74e      chromium_iphone   
4  00b748c3-5c91-43d2-b603-ae43d9fd4be2               chrome   

  browserstack:browser_version browserstack:os browserstack:os_version  \
0                   135.0 beta            OS X                  Sonoma   
1                        134.0         Windows                      11   
2                        124.0            OS X                Monterey   
3                      unknown             ios                    16.2   
4                        118.0            OS X                  Sonoma   

   browserstack:real_height  browserstack:real_width  \
0                      1011                     1200   
1                      1012                      945   
2                      1011                     1200   
3                       669                      390   
4                      1011                     1200   

                                                                                                                                   css:User-Agent  \
0                           Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/135.0.0.0 Safari/537.36   
1                                 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/134.0.0.0 Safari/537.36   
2             Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/124.0.0.0 Safari/537.36 Edg/124.0.0.0   
3  Mozilla/5.0 (iPhone; CPU iPhone OS 16_2 like Mac OS X) AppleWebKit/605.1.15 (KHTML, like Gecko) CriOS/125.0.6422.80 Mobile/15E148 Safari/604.1   
4                           Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/118.0.0.0 Safari/537.36   

  css:browser  css:env-1-height  css:env-1-width  css:env-10-height  \
0      chrome               136              195                166   
1      chrome               136              190                166   
2      chrome               136              195                166   
3      chrome               120              195                166   
4      chrome               136              195                166   

   css:env-10-width  css:env-11-height  css:env-11-width  css:env-12-height  \
0               712              175.0            1100.0                123   
1               732              175.0            1100.0                126   
2               712              175.0            1100.0                123   
3               654              147.0            1100.0                116   
4               712              175.0            1100.0                123   

   css:env-12-width  css:env-13-height  css:env-13-width  css:env-14-height  \
0              6762              125.0              88.0              130.0   
1              6970              130.0              86.0              130.0   
2              6762              125.0              84.0              130.0   
3              6656              116.0              84.0              130.0   
4              6762              125.0              84.0              130.0   

   css:env-14-width  css:env-2-height  css:env-2-width  css:env-3-height  \
0              78.0               188              403               110   
1              78.0               189              403               110   
2              78.0               188              403               110   
3              74.0               150              386               100   
4              78.0               188              403               110   

   css:env-3-width  css:env-5-height  css:env-5-width  css:env-6-height  \
0              133               100              600     

In [90]:
save_features(df_ready)

In [91]:
# list all columns
print(df_ready.columns)

Index(['session_id', 'browserstack:browser', 'browserstack:browser_version',
       'browserstack:os', 'browserstack:os_version',
       'browserstack:real_height', 'browserstack:real_width', 'css:User-Agent',
       'css:browser', 'css:env-1-height', 'css:env-1-width',
       'css:env-10-height', 'css:env-10-width', 'css:env-11-height',
       'css:env-11-width', 'css:env-12-height', 'css:env-12-width',
       'css:env-13-height', 'css:env-13-width', 'css:env-14-height',
       'css:env-14-width', 'css:env-2-height', 'css:env-2-width',
       'css:env-3-height', 'css:env-3-width', 'css:env-5-height',
       'css:env-5-width', 'css:env-6-height', 'css:env-6-width',
       'css:env-7-height', 'css:env-7-width', 'css:env-8-height',
       'css:env-8-width', 'css:env-9-height', 'css:env-9-width',
       'css:image-set-heif', 'css:javascript', 'css:px_per_px', 'css:system',
       'css:viewport_height', 'css:viewport_width',
       'js:env-1-container-height', 'js:env-1-container-width',
 